In [1]:
%load_ext autoreload
%autoreload 2

In [99]:
import numpy as np
import librosa
import torch
from src import laion_clap
from glob import glob
import pandas as pd
import jmespath

In [54]:
# quantization
def int16_to_float32(x):
    return (x / 32767.0).astype(np.float32)


def float32_to_int16(x):
    x = np.clip(x, a_min=-1., a_max=1.)
    return (x * 32767.).astype(np.int16)

In [ ]:
model = laion_clap.CLAP_Module(enable_fusion=False, amodel= 'HTSAT-base')
model.load_ckpt(ckpt="/Users/berkayg/Codes/music-project/laion-clap-project/curate-me-a-playlist/model_checkpoints/music_audioset_epoch_15_esc_90.14.pt")

In [55]:
def load_music_file(file_name):
    audio_data, _ = librosa.load(file_name, sr=48000) # sample rate should be 48000
    audio_data = audio_data.reshape(1, -1) # Make it (1,T) or (N,T)
    # audio_data = torch.from_numpy(int16_to_float32(float32_to_int16(audio_data))).float() # quantize before send it in to the model
    with torch.no_grad():
        audio_embed = model.get_audio_embedding_from_data(x = audio_data, use_tensor=False)
    return audio_embed


In [54]:
with open("/Users/berkayg/Codes/music-project/laion-clap-project/curate-me-a-playlist/data/json/final_track_data.json", "r") as reader:
    track_data = json.load(reader)

In [4]:
music_files = glob("/Users/berkayg/Codes/music-project/AudioCLIP/data/downloaded_tracks/*.wav")

In [5]:
import pickle
with open("/Users/berkayg/Codes/music-project/laion-clap-project/curate-me-a-playlist/data/vectors/song_names.pkl", "rb") as reader:
    ls = pickle.load(reader)


In [69]:
music_data = np.zeros((len(track_data), 512), dtype=np.float32)
track_data_new = []
idx = 0
for m in track_data:
    if m["file_path"]:
        music_data[idx] = load_music_file(m["file_path"])
        dc = m.copy()
        dc.update({"vector_idx": idx})
        track_data_new.append(dc)
        idx += 1


/var/folders/sr/r72219hj06x_1xvw7hhd517h0000gn/T/ipykernel_39391/3009710654.py:2: UserWarning: PySoundFile failed. Trying audioread instead.
  audio_data, _ = librosa.load(file_name, sr=48000) # sample rate should be 48000
/Users/berkayg/miniforge3/envs/playlist-curator/lib/python3.10/site-packages/librosa/core/audio.py:183: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


In [105]:
vector_db_data = track_data_new.copy()
vector_db_data.sort(key=lambda x: x["vector_idx"])
vector_ids = [f"audio_{k['vector_idx']}" for k in vector_db_data]
vector_indices = [k["vector_idx"] for k in vector_db_data]
vector_db_data = jmespath.search("[*].{artist_name: artist_name, track_name: track_name, title: title, link: link, vector_idx: vector_idx}", vector_db_data)

In [110]:
from chromadb import Documents, EmbeddingFunction, Embeddings

class CuratorTextEmbedding(EmbeddingFunction):
    def __call__(self, text: Documents) -> Embeddings:
        # embed the documents somehow
        return embeddings

In [6]:
import chromadb
chroma_client = chromadb.Client()

In [166]:
chroma_client.delete_collection(name="playlist_collection")
collection = chroma_client.create_collection(name="playlist_collection", metadata={"hnsw:space": "ip"})

In [167]:
collection.add(
    embeddings=music_data[vector_indices].tolist(),
    metadatas=vector_db_data,
    ids=vector_ids
    )

In [172]:
collection.query?

Signature:
collection.query(
    query_embeddings: Union[Sequence[float], Sequence[int], List[Union[Sequence[float], Sequence[int]]], NoneType] = None,
    query_texts: Union[str, List[str], NoneType] = None,
    query_images: Union[numpy.ndarray[Any, numpy.dtype[Union[numpy.uint64, numpy.int64, numpy.float64]]], List[numpy.ndarray[Any, numpy.dtype[Union[numpy.uint64, numpy.int64, numpy.float64]]]], NoneType] = None,
    query_uris: Union[str, List[str], NoneType] = None,
    n_results: int = 10,
    where: Optional[Dict[Union[str, Literal['$and'], Literal['$or']], Union[str, int, float, bool, Dict[Union[Literal['$gt'], Literal['$gte'], Literal['$lt'], Literal['$lte'], Literal['$ne'], Literal['$eq'], Literal['$and'], Literal['$or']], Union[str, int, float, bool]], Dict[Union[Literal['$in'], Literal['$nin']], List[Union[str, int, float, bool]]], List[ForwardRef('Where')]]]] = None,
    where_document: Optional[Dict[Union[Literal['$contains'], Literal['$and'], Literal['$or']], Union[str,

In [173]:
text_data = ["romantic, depressing"] 
text_embed = model.get_text_embedding(text_data)
collection.query(query_embeddings=text_embed.tolist(), n_results=10, where={"artist_name": "Coldplay"})

{'ids': [['audio_292',
   'audio_481',
   'audio_298',
   'audio_474',
   'audio_121',
   'audio_476',
   'audio_337',
   'audio_472',
   'audio_225',
   'audio_482']],
 'distances': [[0.6302633285522461,
   0.6571106910705566,
   0.6896730661392212,
   0.7028166055679321,
   0.7428299784660339,
   0.7440136671066284,
   0.7793576717376709,
   0.7837952971458435,
   0.8032999038696289,
   0.8056029081344604]],
 'metadatas': [[{'artist_name': 'Coldplay',
    'link': 'https://www.youtube.com/watch?v=kcASPx3-HuI',
    'title': 'Coldplay - Trouble (Official video)',
    'track_name': 'Trouble',
    'vector_idx': 292},
   {'artist_name': 'Coldplay',
    'link': 'https://www.youtube.com/watch?v=k4V3Mo61fJM',
    'title': 'Coldplay - Fix You (Official Video)',
    'track_name': 'Fix You',
    'vector_idx': 481},
   {'artist_name': 'Coldplay',
    'link': 'https://www.youtube.com/watch?v=57rEQZiklxQ',
    'title': 'See You Soon',
    'track_name': 'See You Soon',
    'vector_idx': 298},
   {'a

In [111]:
text_data = ["This audio is an energetic, uplifting song"] 
text_embed = model.get_text_embedding(text_data)
print(text_embed.shape)

(1, 512)


In [6]:
song_names = [k.split("/")[-1] for k in music_files]

In [52]:
ranking = torch.tensor(audio_vectors) @ torch.tensor(text_embed).t()
ranking = ranking[:, 0].reshape(-1, 1)
print(ranking.shape)

torch.Size([630, 1])


In [53]:
pd.DataFrame(ranking, columns=[text_data[0]], index=song_names).nlargest(15, text_data[0])

This audio is an energetic, uplifting song
Ciara - Can't Leave 'Em Alone (feat. 50 Cent).wav                                     0.423258
The Weeknd - Blinding Lights.wav                                                      0.415049
Stromae - Tous les mêmes.wav                                                          0.412208
Empire of the Sun - Alive.wav                                                         0.373571
Kylie Minogue - Chocolate.wav                                                         0.348002
Sia - Elastic Heart.wav                                                               0.334062
Sia - Chandelier.wav                                                                  0.330263
Stevie Wonder - Signed, Sealed, Delivered (I'm ...                                    0.324698
Coldplay - Princess of China.wav                                                      0.319533
Florence + The Machine - Spectrum (Say My Name)...                                    0.315443
Coldplay - True Love.wav                                                              0.308231
Coldplay - Talk.wav                                                                   0.307894
Lily Allen - Not Fair.wav                                                             0.300576
Andru Donalds - Mishale.wav                                                           0.296594
Linkin Park - Numb.wav                                                                0.294131

In [7]:
import json
import pickle
def load_data():
    vectors = np.load("/Users/berkayg/Codes/music-project/laion-clap-project/curate-me-a-playlist/data/vectors/audio_representations.npy")
    with open("/Users/berkayg/Codes/music-project/laion-clap-project/curate-me-a-playlist/data/vectors/song_names.pkl", "rb") as reader:
        song_names = pickle.load(reader)

    with open("/Users/berkayg/Codes/music-project/laion-clap-project/curate-me-a-playlist/data/json/youtube_data.json", "r") as reader:
        youtube_data = json.load(reader)

    df_youtube = pd.DataFrame(youtube_data)
    df_youtube["id"] = df_youtube["artist_name"] + " - " + df_youtube["track_name"] + ".wav"
    df_youtube.set_index("id", inplace=True)
    return vectors, song_names, df_youtube
audio_vectors, song_names, df_youtube = load_data()

In [44]:
from sklearn.manifold import TSNE
decomposer = TSNE(3)
audio_components = decomposer.fit_transform(np.vstack([audio_vectors, text_embed]))

In [76]:
import plotly.express as px
(torch.tensor(text_embed) / torch.linalg.norm(torch.tensor(text_embed), dim=-1, keepdim=True))
torch.linalg.norm(torch.tensor(audio_vectors), dim=-1, keepdim=True).shape

torch.Size([630, 1])

In [48]:
np.vstack([audio_vectors, text_embed])

array([[-0.0228844 , -0.01531727, -0.02099325, ...,  0.02487872,
        -0.04954423, -0.00967047],
       [ 0.05719518, -0.05181887,  0.02295402, ...,  0.04154928,
        -0.01846843,  0.0015544 ],
       [-0.01932843, -0.03254181, -0.02956614, ...,  0.04285421,
        -0.00225228, -0.00785008],
       ...,
       [-0.05801252,  0.05521129, -0.06229992, ..., -0.02577653,
         0.01485025, -0.04933776],
       [-0.01117569,  0.03371193,  0.03643309, ...,  0.03710453,
         0.06688339,  0.04197252],
       [ 0.02041594, -0.00629344, -0.10389867, ..., -0.02280687,
        -0.02982889,  0.03500484]], dtype=float32)

In [45]:
songs = song_names.copy()
songs.append("text_embedding")

In [46]:
df_vectors = pd.DataFrame(audio_components).assign(song_names=songs, is_text=lambda x: x["song_names"] == "text_embedding")
df_vectors.tail()

0          1          2                          song_names  \
626   7.839409  -2.566209  25.651859        Wilson Pickett - Hey Joe.wav   
627  25.030121  10.993256   2.521003   Bülent Ortaçgil - Değirmenler.wav   
628 -11.422283   6.371774 -33.630165               Sufle - Köprüaltı.wav   
629 -21.544903   7.802368 -11.589836  Keane - Somewhere Only We Know.wav   
630 -32.042549 -20.397856 -20.176537                      text_embedding   

     is_text  
626    False  
627    False  
628    False  
629    False  
630     True

In [47]:
fig = px.scatter_3d(x=0, y=1, z=2, data_frame=df_vectors.tail(100), hover_data={"song_names": True}, color="is_text", opacity=0.8)
fig.show()
